# Estructura de la materia 3
## Trabajo final: DFT de Helio en GS
### PARTE B: Inclusión del potencial de exchange
Mendez, Alejandra

In [83]:
%matplotlib inline

In [84]:
from numpy import sqrt, exp, linspace, zeros, identity, array, diag, c_, pi
from math import factorial
from numpy.linalg import eigh
from scipy.integrate import quad
from scipy.special import hyp1f1
from matplotlib.pyplot import plot, axis, title, xlabel, ylabel, show,\
                              legend, subplot

In [85]:
# Normalización de las funciones 
def Normalizate(U,x):
    h = x[1]-x[0] # assume uniformly spaced points
    n = len(x)
    for j in range(0,n-1):
        suma = 0.0
        for i in range(0,n-1):
             suma = suma + U[i,j]**2
        #suma = suma + U[0,j]/2.0
        suma = suma*h 
        rnorm = 1/sqrt(suma)
#       Normalization
        rsign = 1
        if U[1,j] < 0:
            rsign = -1
        rnorm = rnorm * rsign
        for i in range(0,n):
            U[i,j] = U[i,j]*rnorm
    return  U

In [86]:
def Laplacian(x):
    h = x[1]-x[0] # assume uniformly spaced points
    n = len(x)
    M = -2*identity(n,'d')
    for i in range(1,n):
        M[i,i-1] = M[i-1,i] = 1
    return M/h**2

In [4]:
# Defino las dimensiones de los arrays a utilizar
nsize = 2000
rmax = 10.0
h = rmax/nsize
rmin = h

In [5]:
print(h)

0.005


In [6]:
# Defino las matrices y vectores necesarios
r = linspace(rmin,rmax,nsize)
T = array([nsize,nsize])
Vs = array([nsize,nsize])
U = zeros([nsize,nsize])
H = array([nsize,nsize])
E = array([nsize])

In [7]:
Upp = zeros(nsize)
Up = zeros(nsize)
Zh = zeros(nsize)
Vh = zeros(nsize)
den = zeros(nsize)
Vx = zeros(nsize)

In [8]:
# Defino el sistema a resolver: Helio en el estado fundamental
Z = 2
l = 0

La ecuación de Kohn-Sham está dada por 
\begin{equation}
  \left[-\frac{1}{2}\nabla^2 + V_{\mathrm{s}}\left(n|\mathbf{r}\right)\right] \phi_i = \epsilon_i \phi_i
\end{equation}

donde

\begin{equation}
  V_{\mathrm{s}}(n|\mathbf{r}) = V_{\mathrm{ext}}(r) + V_{\mathrm{H}}(n|\mathbf{r}) + V_{\mathrm{x}}(n|\mathbf{r})
\end{equation}

El potencial de Hartree está dado por:

\begin{equation}
   V_{\mathrm{H}}(r) = \int{d\mathbf{r}\,\frac{n(\mathbf{r}')}{\left|\mathbf{r}-\mathbf{r}'\right|}}
\end{equation}

donde $n=\sum_i{n_i}=\sum_i{\left|\phi_i\right|^2}$ es la densidad total.

\begin{equation}
   \quad \Rightarrow \quad 
   \nabla^2 V_{\mathrm{H}}(n|\mathbf{r}) = -4\pi \, n(\mathbf{r})
\end{equation}

Debido a la simetría radial de la densidad,

\begin{equation}
  Z_{\mathrm{H}}(r) = r V_{\mathrm{H}}(r) 
   \quad \Rightarrow \quad 
   \frac{d^2 Z_{\mathrm{H}}(r)}{dr^2} = -4\pi \, r\,n(r)
\end{equation}

Resolviendo, usando el algoritmo de Verlet, e imponiendo dos condiciones 
de borde

\begin{equation}
  Z_{\mathrm{H}}(0) = 0
  \quad \mbox{y} \quad  
  Z_{\mathrm{H}}(r_{\mathrm{max}}) = q = 2
\end{equation}

Definimos el potencial de exchange según la Local Density Approximation (LDA) formulada por Slater:

\begin{equation}
   V_{\mathrm{x}}(r) = A_{\mathrm{x}}n(r)^{1/3} \quad : \quad A_{\mathrm{x}} = -(3/\pi)^{1/3}
\end{equation}


In [9]:
# Defino la densidad total
def densidad():
    noc = 2.0      # nro de ocupacion = 1 
    ang = 1.0/(4.0*pi)
    for i in range(nsize):
        den[i] = noc*(U[i,0]/r[i])**2*ang
    return den

In [10]:
# Defino el potencial de Hartree
# Uso el índice j (nro de iteracion) para no incluir el potencial Vh en la primera iteración
def VHartree(j):
    if (j>0):
        # 1ra condicion de borde
        Up[0] = 0.0
        Zh[0] = 0.0
        Zh[1] = h
        for i in range(nsize):
            Upp[i] = -4.0*pi*den[i]*r[i]
        for i in range(nsize-1):
            Up[i+1] = Up[i] + 0.5*(Upp[i] + Upp[i+1])*h 
        # 2da condicion de borde
        alfa = -Up[nsize-1]
        for i in range(nsize-1):
            Zh[i+1] = Zh[i] + Up[i]*h + 0.5*Upp[i]*h**2 
        for i in range(nsize):
            Zh[i] = Zh[i] + alfa*r[i]
        for i in range(nsize):
            Vh[i] = Zh[i]/r[i]
    return Vh

In [11]:
# Defino el potencial de Exchange: Local Density Approximation
# Nuevamente uso j para no incluir el potencial en la primera iteración
def Vexchange(j):
    if (j>0):
        Ax = -(3./pi)**(1./3.)
        for i in range(nsize):
            Vx[i] = Ax*(den[i])**(1./3.)
    return Vx

In [12]:
# Inicializo algunas variables utiles en la iteración
# j : nro de iteraciones
j = 0
Eorb = []
u0 = zeros((nsize,1))

## Empieza loop

In [75]:
# Calculo la densidad, el potencial de Hartree y potencial de Exchange LDA
densidad()
VHartree(j)
Vexchange(j)

# Construyo el operador T y el operador Vs (potencial efectivo)
T = (-0.5)*Laplacian(r)
Vs = -Z/r + l*(l+1)/(2*r**2) + Vh + Vx

In [76]:
# Construyo el Hamiltoniano del sistema
H =  T + diag(Vs)

In [77]:
# Calculo autovalores (E) y autovectores (U)
E,U = eigh(H)
j = j + 1

# Normalization
U = Normalizate(U,r)

In [78]:
# Corroboro normalización
suma = 0.0
for i in range(nsize):
    suma = suma + (U[i,0])**2
suma = suma*h
suma

1.000000000000008

In [79]:
# Adjunto los resultados para ver los resultados de cada iteración
# Eorb : energías
# u0   : funciones radiales reducidas
Eorb.append(E[0])
Eorb

[-1.9999500024997479,
 -0.32098913995646172,
 -0.62817500564042394,
 -0.4715087067081225,
 -0.53890139235045675,
 -0.50709381788626695,
 -0.5215245398996976,
 -0.51485365883598433,
 -0.51791135002262956,
 -0.51650430191096286,
 -0.51715061527484962]

In [80]:
u0 = c_[u0,U[:,0]]
u0

array([[  0.00000000e+00,   2.80021427e-02,   2.06288958e-02, ...,
          2.31358180e-02,   2.31205302e-02,   2.31275571e-02],
       [  0.00000000e+00,   5.54470427e-02,   4.08479336e-02, ...,
          4.58116008e-02,   4.57813313e-02,   4.57952445e-02],
       [  0.00000000e+00,   8.23430168e-02,   6.06639000e-02, ...,
          6.80345985e-02,   6.79896509e-02,   6.80103108e-02],
       ..., 
       [  0.00000000e+00,   6.57646999e-09,   1.74094903e-05, ...,
          3.62148370e-06,   3.65904839e-06,   3.64173987e-06],
       [  0.00000000e+00,   4.38398456e-09,   1.16061716e-05, ...,
          2.41427037e-06,   2.43931310e-06,   2.42777427e-06],
       [  0.00000000e+00,   2.19189365e-09,   5.80303925e-06, ...,
          1.20711956e-06,   1.21964080e-06,   1.21387144e-06]])

## Termina loop

La energía total en este esquema está dada por:

\begin{equation}
  E = \sum_i\epsilon_i - E_{\mathrm{H}} - E_{\mathrm{x}}
\end{equation}
siendo

\begin{equation}
  E_{\mathrm{H}} = \frac{1}{2} \int{dr \,V_{\mathrm{H}}(r)\,n(r) } \quad \mbox{y} \quad
  E_{\mathrm{x}} = \frac{1}{2} \int{dr \,V_{\mathrm{x}}(r)\,n(r) } 
\end{equation}

In [81]:
# Calculo la integral del potencial Vh
suma = 0.0
for i in range(nsize):
    suma = suma + Vh[i]*(U[i,0]**2)
Eh = suma*h
print('Eh = ',Eh)
# Calculo la integral del potencial Vx
suma = 0.0
for i in range(nsize):
    suma = suma + Vx[i]*(U[i,0]**2)
Ex = 0.5*suma*h
print('Ex = ',Ex)

Eh =  1.97379162952
Ex =  -0.284260310217


### Exchange LDA : -0.268 a.u.  
### Exchange HF: -0.313

In [82]:
# Calculo la energia total del sistema
for i in range(j):
    if (i==0):
        Etot = 2.0*(Eorb[i])
    else:
        Etot = 2.0*(Eorb[i]) - Eh - Ex
    print('# de iteracion:',i,'  Etot = ',Etot)

# de iteracion: 0   Etot =  -3.999900005
# de iteracion: 1   Etot =  -2.33150959921
# de iteracion: 2   Etot =  -2.94588133058
# de iteracion: 3   Etot =  -2.63254873272
# de iteracion: 4   Etot =  -2.767334104
# de iteracion: 5   Etot =  -2.70371895507
# de iteracion: 6   Etot =  -2.7325803991
# de iteracion: 7   Etot =  -2.71923863697
# de iteracion: 8   Etot =  -2.72535401935
# de iteracion: 9   Etot =  -2.72253992312
# de iteracion: 10   Etot =  -2.72383254985


### Energía total HF : -2.861680